In [46]:
token=''
with open('.token', 'r') as f:
    token = f.read().strip()

In [6]:
import requests
#Read .token file

root = "https://www.ensembledata.com/apis"
endpoint = "/tt/user/posts"
params = {
  "username": "lilmiquela",
  "depth": 50,
  "start_cursor": 0,
  "oldest_createtime": 0,
  "token": token
}


res = requests.get(root+endpoint, params=params)
print(res.json())
#Save response to file
with open('lilmiquela_posts.json', 'w') as f:
    f.write(res.text)

{'data': [{'ad_aweme_source': 1, 'added_sound_music_info': {'album': 'Choices (Yup)', 'artists': [], 'audition_duration': 60, 'author': 'Lil Skeet', 'author_deleted': False, 'author_position': None, 'binded_challenge_id': 0, 'can_not_reuse': False, 'collect_stat': 0, 'commercial_right_type': 1, 'cover_hd': {'height': 720, 'uri': 'tos-alisg-v-2774/072ec23b91234f69b210a1aa61d251c5', 'url_list': ['https://p16-sg.tiktokcdn.com/aweme/1080x1080/tos-alisg-v-2774/072ec23b91234f69b210a1aa61d251c5.jpeg'], 'url_prefix': None, 'width': 720}, 'cover_large': {'height': 720, 'uri': 'tos-alisg-v-2774/072ec23b91234f69b210a1aa61d251c5', 'url_list': ['https://p16-sg.tiktokcdn.com/aweme/720x720/tos-alisg-v-2774/072ec23b91234f69b210a1aa61d251c5.jpeg'], 'url_prefix': None, 'width': 720}, 'cover_medium': {'height': 720, 'uri': 'tos-alisg-v-2774/072ec23b91234f69b210a1aa61d251c5', 'url_list': ['https://p16-sg.tiktokcdn.com/aweme/200x200/tos-alisg-v-2774/072ec23b91234f69b210a1aa61d251c5.jpeg'], 'url_prefix': No

The next fragment of code is used to collect all hashtags from the posts, that way we can select which one to use as a flag to identify 'past' and 'present' posts

In [2]:

import json
#read file as a string
with open('lilmiquela_posts.json', 'r') as f:
    data = f.read()
#convert string to json
data = json.loads(data)
all_hashtags = []
for post in data['data']:
    #Get all the words appearing after #
    hashtags = [word for word in post['desc'].split() if word[0] == '#']
    #Remove # from hashtags
    hashtags = [word[1:] for word in hashtags]
    #convert to lower case
    hashtags = [word.lower() for word in hashtags]
    #Add hashtags to list
    all_hashtags.append(hashtags)
#remove all duplicates from list
all_hashtags = list(set([item for sublist in all_hashtags for item in sublist]))
print(all_hashtags)
#Save hashtags to csv file
with open('lilmiquela_hashtags.csv', 'w') as f:
    f.write('\n'.join(all_hashtags))


['squidgame', 'vibing', 'notjustme', 'gaminglife', 'whenimolder', '16missedcalls', 'foodontiktok', 'driverslicense', 'illneverforgetyou', 'nickiminaj', 'taylorswift', 'doaflip', 'bts', 'fitcheck', 'challenge', 'andithinktomyself', 'countdown', 'naturescereal', 'distancedance', 'karpoolkaraoke', 'duet', 'makeup', 'joselinescabaret', 'kendricklamar', 'fyp', 'friends', 'unrealisticchristmaslist', 'metaverse', 'crazy', 'music', 'feliznavidad', 'wewintogether', 'filter', 'isthisavailable', 'pacsun', 'backintheday', 'dior', 'rating', 'maybewhenimdancing', 'sciencetok', 'teenagedirtbag', 'taurus', 'lifeisgood', 'waitforit', 'bitcoin', 'robotgirl', 'wrappinggifts', 'good4u', 'fypシ', 'society', 'manifesting', 'immuneupvapedown', 'rhymepov', 'charging', 'couplethings', 'iiipoints', 'healthyliving', 'food', 'life', 'runningqueen', 'casualfashion', 'checkyourvibe', 'springvibes', 'adayinmylife', 'onethingaboutme', 'spelling', 'relatable', 'mamasaid', 'everydayolympics', 'transformation', 'whatwill

Now we get all the statistics from each post, we split them in 2 lists (one for present and one for past), and we get the id of the 3 best and 3 worst post of the two categories

In [32]:

import json
#read file as a string
with open('lilmiquela_posts.json', 'r') as f:
    data = f.read()
#convert string to json
data = json.loads(data)
#Get post titles
#Def empty matrix
posts = {}
#Define a list of flags that define throwback posts
past_flags= ['whenimolder', 'illneverforgetyou', 'backintheday', 'teenagedirtbag', 'waitforit', 'transformation', 'whatwillilooklike', 'notaperfectperson', 'dejavu', 'ohtakemebacktothenightwemet', 'evolution', 'breakup', 'upgradechallenge', 'yearinreview', '2018vs2021', 'mylife', 'beentheredonethat', 'storytime', '2020rewind', 'justdancemoves', 'crazystory', '2021rewind', 'timewarpjump', 'deeprealization', 'yearontiktok', 'leftmeonread', 'breakuptiktok', 'throwback', 'beforeandafter']
past_posts = {}
present_posts = {}

i=0
for post in data['data']:
    posts[i]=[post['aweme_id'],post['desc'],post['statistics']['play_count'],post['statistics']['digg_count'],post['statistics']['comment_count'],post['statistics']['share_count']]
    #Check if post is a throwback post
    #Get all the words appearing after #
    hashtags = [word for word in post['desc'].split() if word[0] == '#']
    #Remove # from hashtags
    hashtags = [word[1:] for word in hashtags]
    #convert to lower case
    hashtags = [word.lower() for word in hashtags]
    #Check if any of the hashtags is a past flag
    for hashtag in hashtags:
        if hashtag in past_flags:
            past_posts[i] = posts[i]
        else:
            present_posts[i] = posts[i]
    #print(posts[i])
    i+=1

print(past_posts.__len__())






26


Below a test to see if NLP emotional reading works

In [48]:
import requests

root = "https://www.ensembledata.com/apis"
endpoint = "/tt/post/comments"
params = {
  "aweme_id": present_posts[0][0],
  "cursor": 0,
  "token": token
}

res = requests.get(root+endpoint, params=params)
print(res.json())


{'data': {'nextCursor': 30, 'comments': [{'author_pin': False, 'aweme_id': '6857638022805032197', 'cid': '6857649495153803270', 'collect_stat': 0, 'comment_language': '', 'comment_post_item_ids': None, 'create_time': 1596670950, 'digg_count': 35189, 'image_list': None, 'is_author_digged': False, 'label_list': [{'text': 'Creator', 'type': 1}], 'label_text': 'Creator', 'label_type': 1, 'no_show': False, 'reply_comment': None, 'reply_comment_total': 333, 'reply_id': '0', 'reply_to_reply_id': '0', 'share_info': {'acl': {'code': 1, 'extra': '{"item_share_acl":"empty item value"}'}, 'desc': "MIQUELA's comment: Forgot to answer: “do u date humans?” 🙃", 'title': 'What’s Polar Express? #ReplyToComments #NopeYup #CheckYourVibe', 'url': 'https://m.tiktok.com/v/6857638022805032197.html?_d=e7i3ehmbm7752f&comment_author_id=6671266312193589253&preview_pb=0&share_comment_id=6857649495153803270&share_item_id=6857638022805032197&sharer_language=en&source=h5_m&u_code=0'}, 'status': 1, 'stick_position': 0

In [57]:

import nltk
nltk.download('punkt')
import pandas as pd
from nltk import word_tokenize
from nltk.stem.snowball import SnowballStemmer
import requests
from LeXmo import LeXmo


data = res.json()
for resp in data['data']['comments']:
    comm= resp['share_info']['desc'].split(':')[1]
    print(comm)
    emo=LeXmo.LeXmo(comm)
    emo.pop('text')
    print(emo)
    



[nltk_data] Downloading package punkt to
[nltk_data]     /Users/alessandrodiscalzi/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


 Forgot to answer
{'anger': 0.0, 'anticipation': 0.0, 'disgust': 0.0, 'fear': 0.0, 'joy': 0.0, 'negative': 0.0, 'positive': 0.0, 'sadness': 0.0, 'surprise': 0.0, 'trust': 0.0}
 She is not a robot guys.
{'anger': 0.0, 'anticipation': 0.0, 'disgust': 0.0, 'fear': 0.0, 'joy': 0.0, 'negative': 0.0, 'positive': 0.0, 'sadness': 0.0, 'surprise': 0.0, 'trust': 0.0}
 Polar express u never wat he’s it 😳 u gots to see it👌🏾
{'anger': 0.0, 'anticipation': 0.0, 'disgust': 0.0, 'fear': 0.0, 'joy': 0.0, 'negative': 0.0, 'positive': 0.0, 'sadness': 0.0, 'surprise': 0.0, 'trust': 0.0}
 can u post a swimming video
{'anger': 0.0, 'anticipation': 0.16666666666666666, 'disgust': 0.0, 'fear': 0.16666666666666666, 'joy': 0.16666666666666666, 'negative': 0.0, 'positive': 0.16666666666666666, 'sadness': 0.0, 'surprise': 0.0, 'trust': 0.0}
 I am so confused 😭
{'anger': 0.0, 'anticipation': 0.0, 'disgust': 0.0, 'fear': 0.0, 'joy': 0.0, 'negative': 0.0, 'positive': 0.0, 'sadness': 0.0, 'surprise': 0.0, 'trust': 0.